In [3]:
import pandas as pd
import folium
from folium.plugins import MarkerCluster
import plotly.express as px
from IPython.display import display

In [27]:
city_df = pd.read_parquet('../data/processed/city_golf_metrics.parquet')
# load user-provided city coordinates (e.g., data/uscities.csv)
city_coords = pd.read_csv('../data/uscities.csv')
# normalize coordinate column names if needed
if 'lng' in city_coords.columns and 'lat' in city_coords.columns:
    city_coords = city_coords.rename(columns={'lng': 'lon', 'lat': 'lat'})
if 'state_id' in city_coords.columns and 'state' not in city_coords.columns:
    city_coords = city_coords.rename(columns={'state_name': 'state'})
# merge on city + state
merge_cols = ['city','state']
coords_use = [c for c in ['city','state','lat','lon'] if c in city_coords.columns]
city_df = city_df.merge(city_coords[coords_use].drop_duplicates(), how='left', on=['city','state'])
# standardize column names
city_df = city_df.sort_values('num_golf_courses', ascending=False)
city_df_cleaned = city_df.dropna(subset=["lat","lon"]).reset_index(drop=True) 
city_df_cleaned.describe()


num_golf_courses   avg_rating  sum_ratings_count  avg_length_yards  \
count       4571.000000  4571.000000        4571.000000       4293.000000   
mean           1.998687     4.150477         389.921461       5485.365362   
std            2.531638     0.513101        1419.766960       1772.750268   
min            1.000000     3.000000           1.000000          0.000000   
25%            1.000000     3.860000           3.000000       4640.700000   
50%            1.000000     4.130000          33.000000       6300.000000   
75%            2.000000     4.500000         275.000000       6691.000000   
max           49.000000     5.000000       29150.000000      10077.000000   

       state_golfable        score         rank          lat          lon  
count          4571.0  4571.000000  4571.000000  4571.000000  4571.000000  
mean              0.0     0.259832  2809.098447    38.936494   -91.534165  
std               0.0     0.114452  1604.167375     5.052663    14.755054  
min               0.0     0.000000     1.000000    18.333100  -159.480100  
25%               0.0     0.197005  1431.500000    35.441050   -96.914850  
50%               0.0     0.260909  2787.000000    39.889000   -87.703500  
75%               0.0     0.341840  4205.000000    42.245900   -81.440450  
max               0.0     0.718229  5585.000000    64.835300   -65.658900

In [11]:
center_lat = city_df_cleaned['lat'].mean()
center_lon = city_df_cleaned['lon'].mean()
m = folium.Map(location=[center_lat, center_lon], zoom_start=5, tiles='CartoDB positron')
mc = MarkerCluster().add_to(m)
# compute rating min/max for normalization
min_rating = city_df_cleaned['avg_rating'].min() if 'avg_rating' in city_df_cleaned.columns else None
max_rating = city_df_cleaned['avg_rating'].max() if 'avg_rating' in city_df_cleaned.columns else None
for _, r in city_df_cleaned.iterrows():
    popup = folium.Popup(f"<b>{r['city']}, {r.get('state','')}</b><br/>Courses: {r['num_golf_courses']}<br/>Avg rating: {r.get('avg_rating', 'n/a')}", max_width=300)
    # radius larger for higher average rating (normalized)
    if pd.notna(r.get('avg_rating')) and min_rating is not None and max_rating is not None and max_rating>min_rating:
        norm = (r['avg_rating'] - min_rating) / (max_rating - min_rating + 1e-9)
        radius = 4 + norm * 20  # range approx 4-24
        if r['avg_rating'] >= 4.0:
            color = 'darkgreen'
        elif r['avg_rating'] >= 3.5:
            color = 'orange'
        else:
            color = 'red'
    else:
        # fallback: size by number of courses
        radius = 4 + (r['num_golf_courses']**0.5)
        color = 'blue'
    folium.CircleMarker(location=[r['lat'], r['lon']], radius=radius, color=color, fill=True, fill_opacity=0.7, popup=popup).add_to(mc)

display(m)

In [6]:
from folium.plugins import HeatMap
heat_df = city_df.dropna(subset=['lat','lon']).copy()
if heat_df.empty:
    print('No centroids available for heatmaps (no lat/lon in city data).')
else:
    # --- Density heatmap (weight = number of golf courses in city) ---
    vals = heat_df['num_golf_courses'].fillna(0).astype(float)
    if vals.max() == vals.min():
        weights = [1.0] * len(vals)
    else:
        weights = ((vals - vals.min()) / (vals.max() - vals.min())).tolist()
    density_data = [[r['lat'], r['lon'], float(w)] for r, w in zip(heat_df.to_dict('records'), weights)]
    hm_density = folium.Map(location=[heat_df['lat'].mean(), heat_df['lon'].mean()], zoom_start=5, tiles='CartoDB positron')
    HeatMap(density_data, radius=20, blur=10, max_zoom=6).add_to(hm_density)
    folium.LayerControl().add_to(hm_density)
    display(hm_density)

    # --- Rating heatmap (weight = avg_rating normalized) ---
    if 'avg_rating' in heat_df.columns:
        vals = heat_df['avg_rating'].fillna(0).astype(float)
        if vals.max() == vals.min():
            weights = [1.0] * len(vals)
        else:
            weights = ((vals - vals.min()) / (vals.max() - vals.min())).tolist()
        rating_data = [[r['lat'], r['lon'], float(w)] for r, w in zip(heat_df.to_dict('records'), weights)]
        hm_rating = folium.Map(location=[heat_df['lat'].mean(), heat_df['lon'].mean()], zoom_start=5, tiles='CartoDB positron')
        HeatMap(rating_data, radius=20, blur=10, max_zoom=6).add_to(hm_rating)
        folium.LayerControl().add_to(hm_rating)
        display(hm_rating)
    else:
        print('No avg_rating available for rating heatmap.')

In [31]:
#(Re)load courses and import compute_metrics from the script
import importlib.util
from pathlib import Path
spec = importlib.util.spec_from_file_location("compute_city_metrics", str(Path('..') / 'eda' / 'compute_city_metrics.py'))
compute_mod = importlib.util.module_from_spec(spec)
spec.loader.exec_module(compute_mod)
compute_metrics = compute_mod.compute_metrics

courses = pd.read_parquet('../data/processed/teeradar_courses.parquet')

# compute without state_golfable
scores_no_state = compute_metrics(courses, weights=None, state_golfable_csv=None)
# compute with state_golfable
scores_with_state = compute_metrics(courses, weights=None, state_golfable_csv='../data/state_golfable_year_round.csv')
print('Top cities (including state_golfable)')
display(scores_with_state.head(20))
print('\nTop cities (excluding state_golfable)')
display(scores_no_state.head(20))

Top cities (including state_golfable)


city           state  num_golf_courses  avg_rating  \
0              Orlando         Florida                69        1.88   
1           Scottsdale         Arizona                50        3.13   
2              Phoenix         Arizona                31        3.26   
3               Naples         Florida                75        3.03   
4            Las Vegas          Nevada                38        3.59   
5                 Mesa         Arizona                30        3.10   
6               Tucson         Arizona                37        3.20   
7            Bradenton         Florida                26        3.24   
8   Hilton Head Island  South Carolina                22        4.07   
9            Kissimmee         Florida                16        3.52   
10         Palm Desert      California                31        2.89   
11          Fort Myers         Florida                37        3.22   
12            Bluffton  South Carolina                19        3.46   
13              Austin           Texas                31        3.74   
14            Sarasota         Florida                24        3.46   
15           La Quinta      California                19        3.52   
16            Sun City         Arizona                12        3.73   
17               Miami         Florida                22        3.73   
18               Tampa         Florida                23        3.39   
19        Green Valley         Arizona                 9        4.00   

    sum_ratings_count  avg_length_yards  state_golfable     score  rank  
0               31232            6392.4               0  0.507354     1  
1               27769            6449.9               0  0.503480     2  
2               30589            5712.4               0  0.493589     3  
3               18858            6422.2               0  0.476417     4  
4               23882            6445.9               0  0.469131     5  
5               24988            4755.6               0  0.435358     6  
6               21266            5461.6               0  0.424672     7  
7               20965            5877.3               0  0.400739     8  
8               14272            6400.9               0  0.379224     9  
9               17982            5626.8               0  0.368889    10  
10              18111            5268.3               0  0.368821    11  
11               8847            5710.1               0  0.321035    12  
12              11585            5909.5               0  0.318317    13  
13               6562            5583.8               0  0.316168    14  
14               9780            5112.5               0  0.313759    15  
15               9860            6820.9               0  0.306733    16  
16              10045            5562.1               0  0.304559    17  
17               6821            6196.9               0  0.298540    18  
18               8609            6115.5               0  0.297717    19  
19               8209            6746.1               0  0.296532    20


Top cities (excluding state_golfable)


city           state  num_golf_courses  avg_rating  \
0              Orlando         Florida                69        1.88   
1           Scottsdale         Arizona                50        3.13   
2               Naples         Florida                75        3.03   
3              Phoenix         Arizona                31        3.26   
4            Las Vegas          Nevada                38        3.59   
5                 Mesa         Arizona                30        3.10   
6               Tucson         Arizona                37        3.20   
7            Bradenton         Florida                26        3.24   
8   Hilton Head Island  South Carolina                22        4.07   
9          Palm Desert      California                31        2.89   
10           Kissimmee         Florida                16        3.52   
11          Fort Myers         Florida                37        3.22   
12              Austin           Texas                31        3.74   
13            Sarasota         Florida                24        3.46   
14            Bluffton  South Carolina                19        3.46   
15         San Antonio           Texas                32        3.20   
16           La Quinta      California                19        3.52   
17             Houston           Texas                43        2.67   
18               Tampa         Florida                23        3.39   
19               Miami         Florida                22        3.73   

    sum_ratings_count  avg_length_yards     score  rank  
0               31232            6392.4  0.757484     1  
1               27769            6449.9  0.729223     2  
2               18858            6422.2  0.723635     3  
3               30589            5712.4  0.692960     4  
4               23882            6445.9  0.668944     5  
5               24988            4755.6  0.614296     6  
6               21266            5461.6  0.608598     7  
7               20965            5877.3  0.563388     8  
8               14272            6400.9  0.529908     9  
9               18111            5268.3  0.527018    10  
10              17982            5626.8  0.508866    11  
11               8847            5710.1  0.470760    12  
12               6562            5583.8  0.456990    13  
13               9780            5112.5  0.445272    14  
14              11585            5909.5  0.445254    15  
15               7234            5915.5  0.430794    16  
16               9860            6820.9  0.429847    17  
17               6042            6318.8  0.424644    18  
18               8609            6115.5  0.422720    19  
19               6821            6196.9  0.422599    20

In [32]:
# Cell 6: Plotly bar charts (top 20) - with state_golfable
top_n = 20
with_state_top = scores_with_state.head(top_n).sort_values('score')
fig1 = px.bar(with_state_top, x='score', y='city', orientation='h', color='state_golfable' if 'state_golfable' in with_state_top.columns else None, title='Top cities (score includes state_golfable)')
fig1.update_layout(height=700, yaxis={'categoryorder':'total ascending'})
fig1.show()

# without state_golfable
without_state_top = scores_no_state.head(top_n).sort_values('score')
fig2 = px.bar(without_state_top, x='score', y='city', orientation='h', title='Top cities (no state_golfable)')
fig2.update_layout(height=700, yaxis={'categoryorder':'total ascending'})
fig2.show()

In [35]:
merged = scores_with_state[['city','state','rank','score']].merge(scores_no_state[['city','state','rank','score']], on=['city','state'], suffixes=('_with','_without'))
merged['rank_change'] = merged['rank_without'] - merged['rank_with']
# filter for cities ranked 20-50 in either scoring method
filtered = merged[((merged['rank_with'] >= 0) & (merged['rank_with'] <= 50)) | ((merged['rank_without'] >= 0) & (merged['rank_without'] <= 50))]
filtered = filtered.sort_values('rank_change', key=lambda s: s.abs(), ascending=False).head(50)

from IPython.display import display
print('Top 50 cities ranked 1-50 in either scoring method (sorted by absolute rank change)')
display(filtered[['city','state','rank_with','rank_without','rank_change','score_with','score_without']])

Top 50 cities ranked 1-50 in either scoring method (sorted by absolute rank change)


city           state  rank_with  rank_without  \
656            Charlotte  North Carolina        657            42   
498         Indianapolis         Indiana        499            32   
79             Pinehurst  North Carolina         80            48   
33               Houston           Texas         34            18   
35            Cincinnati            Ohio         36            22   
38             San Diego      California         39            26   
44              Monterey      California         45            57   
43             Daly City      California         44            56   
47          Jacksonville         Florida         48            37   
40      New Smyrna Beach         Florida         41            50   
48            Mamaroneck        New York         49            58   
24               Buckeye         Arizona         25            34   
49            Banner Elk  North Carolina         50            59   
31                Peoria         Arizona         32            40   
39   Egg Harbor Township      New Jersey         40            47   
28         Sun City West         Arizona         29            36   
20              Clermont         Florida         21            28   
19          Green Valley         Arizona         20            27   
41      Fernandina Beach         Florida         42            49   
21           San Antonio           Texas         22            16   
51            Clearwater         Florida         52            46   
34         Miramar Beach         Florida         35            41   
29           Punta Gorda         Florida         30            35   
37            Palm Coast         Florida         38            43   
32             Davenport         Florida         33            38   
27          Myrtle Beach  South Carolina         28            23   
25               Raleigh  North Carolina         26            30   
42              Portland          Oregon         43            39   
16              Sun City         Arizona         17            21   
26             Henderson          Nevada         27            31   
36           Los Angeles      California         37            33   
17                 Miami         Florida         18            20   
12              Bluffton  South Carolina         13            15   
30               Atlanta         Georgia         31            29   
45              Lakeland         Florida         46            44   
46    North Myrtle Beach  South Carolina         47            45   
15             La Quinta      California         16            17   
13                Austin           Texas         14            13   
9              Kissimmee         Florida         10            11   
10           Palm Desert      California         11            10   
3                 Naples         Florida          4             3   
2                Phoenix         Arizona          3             4   
22              Chandler         Arizona         23            24   
14              Sarasota         Florida         15            14   
23                 Ocala         Florida         24            25   
18                 Tampa         Florida         19            19   
1             Scottsdale         Arizona          2             2   
7              Bradenton         Florida          8             8   
6                 Tucson         Arizona          7             7   
11            Fort Myers         Florida         12            12   

     rank_change  score_with  score_without  
656         -615    0.254163       0.375740  
498         -467    0.262339       0.392695  
79           -32    0.263671       0.366493  
33           -16    0.280874       0.424644  
35           -14    0.275865       0.414333  
38           -13    0.273674       0.404122  
44            12    0.268353       0.360558  
43            12    0.268449       0.360686  
47           -11    0.267677       0.383983  
40             9    0.271125       0.365

In [36]:
# State-level analysis
state_analysis = city_df.groupby('state').agg({
    'num_golf_courses': 'sum',
    'sum_ratings_count': 'sum',
    'avg_rating': 'mean'
}).reset_index().rename(columns={'num_golf_courses': 'total_courses', 'sum_ratings_count': 'total_ratings'})

# build an aggregate score combining volume and quality
state_analysis[['total_courses','total_ratings','avg_rating']] = state_analysis[['total_courses','total_ratings','avg_rating']].fillna(0)

def _minmax(series):
    rng = series.max() - series.min()
    if rng == 0:
        return pd.Series([1.0] * len(series), index=series.index)
    return (series - series.min()) / rng

state_analysis['score'] = (
    0.4 * _minmax(state_analysis['total_courses']) +
    0.3 * _minmax(state_analysis['total_ratings']) +
    0.3 * _minmax(state_analysis['avg_rating'])
)

state_analysis = state_analysis.sort_values('score', ascending=False)

print('Golf Metrics by State (with aggregate score)')
display(state_analysis)

Golf Metrics by State (with aggregate score)


state  total_courses  total_ratings  avg_rating     score
10                Florida            833         463359    4.082573  0.800559
5              California            747         281305    4.116791  0.648781
23               Michigan            621          55901    4.133067  0.445805
45                  Texas            491         107406    4.061467  0.401087
33               New York            494          42537    4.218195  0.394601
2                 Arizona            306         223354    4.089385  0.393284
36                   Ohio            526          52701    4.103439  0.391619
14               Illinois            422          76561    4.173975  0.372401
39           Pennsylvania            470          41931    4.118671  0.361034
34         North Carolina            421          65243    4.136650  0.356478
11                Georgia            302          74897    4.135333  0.305231
42         South Carolina            275          69972    4.186796  0.300249
4   Armed Forces Americas              1              2    5.000000  0.300000
51              Wisconsin            318          19144    4.222217  0.295714
31             New Jersey            230          65301    4.261224  0.291771
24              Minnesota            284          10851    4.276784  0.285861
48               Virginia            239          34464    4.278595  0.279908
15                Indiana            313          21933    4.071026  0.262248
22          Massachusetts            248          22624    4.202428  0.260011
6                Colorado            183          17895    4.278118  0.242154
26               Missouri            187          20009    4.114167  0.209804
49             Washington            188          17344    4.108230  0.207269
18               Kentucky            176          13420    4.145849  0.207137
38                 Oregon            149          13135    4.200641  0.205883
28               Nebraska            146           3327    4.212418  0.200651
29                 Nevada             88          45178    4.213125  0.200016
44              Tennessee            196          21326    4.041250  0.199132
47                Vermont             42           1001    4.417250  0.193674
16                   Iowa            165           2054    4.133934  0.191900
8                Delaware             29           7569    4.411250  0.190372
13                  Idaho             68           1083    4.328261  0.186881
17                 Kansas             96           3475    4.254308  0.185815
52                Wyoming             26            156    4.409048  0.183651
41           Rhode Island             38           2274    4.350714  0.178110
30          New Hampshire             79           4579    4.244444  0.176212
46                   Utah             93           2211    4.213200  0.174618
27                Montana             58            833    4.293947  0.174452
19              Louisiana             90          11344    4.171731  0.170073
37               Oklahoma            119           5441    4.112295  0.167273
7             Connecticut            117          15792    4.083600  0.166775
20                  Maine             72           1128    4.225254  0.166441
12                 Hawaii             65          15007    4.198000  0.166136
40            Puerto Rico             11            464    4.355000  0.164889
21               Maryland            122          21351    4.030260  0.161182
0                 Alabama            127          13664    4.015811  0.155468
43           South Dakota             44            619    4.215455  0.150519
25            Mississippi             65           4347    4.157778  0.150491
35           North Dakota             55            216    4.170000  0.145665
50          West Virginia             57           1704    4.156250  0.144601
3                Arkansas             93           3869    3.995000  0.128256
32             New Mexico             46  